# To enable using GPU instead of CPU

In [2]:
pip install torch==2.2.1+cu121 torchvision==0.17.1+cu121 -f https://download.pytorch.org/whl/torch_stable.html

^C
Note: you may need to restart the kernel to use updated packages.


# Check if using GPU or CPU in training and running app

In [1]:
import torch
torch.cuda.is_available()

True

# Check your GPU details

In [2]:
!nvidia-smi

Thu Mar 14 23:53:15 2024       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 551.76                 Driver Version: 551.76         CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                     TCC/WDDM  | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA GeForce GTX 1080      WDDM  |   00000000:01:00.0  On |                  N/A |
| 25%   54C    P0             47W /  238W |    1232MiB /   8192MiB |      6%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

# Open Camera and try model

## original code wtihout modification

In [ ]:
from ultralytics import YOLO
import cv2
import math
# start webcam
cap = cv2.VideoCapture(0)
cap.set(3, 640)
cap.set(4, 480)

# model
# model = YOLO("runs/detect/train14/weights/best.pt")
model = YOLO("runs/detect/train36/weights/best.pt")

# object classes
classNames = [ "male"]


while True:
    success, img = cap.read()
    results = model(img, stream=True)

    # coordinates
    for r in results:
        boxes = r.boxes

        for box in boxes:
            # bounding box
            x1, y1, x2, y2 = box.xyxy[0]
            x1, y1, x2, y2 = int(x1), int(y1), int(x2), int(y2) # convert to int values

            # put box in cam
            cv2.rectangle(img, (x1, y1), (x2, y2), (255, 0, 255), 3)

            # confidence
            confidence = math.ceil((box.conf[0]*100))/100
            print("Confidence --->",confidence)

            # class name
            cls = int(box.cls[0])
            print("Class name -->", classNames[cls])

            # object details
            org = [x1, y1]
            font = cv2.FONT_HERSHEY_SIMPLEX
            fontScale = 1
            color = (255, 0, 0)
            thickness = 2

            cv2.putText(img, classNames[cls], org, font, fontScale, color, thickness)

    cv2.imshow('Webcam', img)
    if cv2.waitKey(1) == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()


0: 480x640 1 male, 52.9ms
Confidence ---> 0.71
Class name --> male
Speed: 3.0ms preprocess, 52.9ms inference, 103.2ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 male, 9.0ms
Confidence ---> 0.71
Class name --> male
Speed: 2.0ms preprocess, 9.0ms inference, 2.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 male, 8.0ms
Confidence ---> 0.71
Class name --> male
Speed: 2.0ms preprocess, 8.0ms inference, 2.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 male, 9.0ms
Confidence ---> 0.71
Class name --> male
Speed: 1.0ms preprocess, 9.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 male, 15.5ms
Confidence ---> 0.71
Class name --> male
Speed: 1.0ms preprocess, 15.5ms inference, 4.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 male, 9.0ms
Confidence ---> 0.71
Class name --> male
Speed: 1.0ms preprocess, 9.0ms inference, 3.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 ma

## Run model (detect only confidence above 50%) + conf label enabled

In [ ]:
from ultralytics import YOLO
import cv2
import math

# Start webcam
cap = cv2.VideoCapture(0)
cap.set(3, 640)
cap.set(4, 480)

# Load YOLO model
model = YOLO("runs/detect/train68/weights/best.pt")

# Object classes
classNames = ['Cup', 'Laptop', 'female', 'headphone', 'keyboard', 'male', 'pen', 'phone', 'shoes', 'glasses']

while True:
    success, img = cap.read()
    results = model(img, stream=True)

    # Process detection results
    for r in results:
        boxes = r.boxes

        for box in boxes:
            # Extract confidence and class name
            confidence = round(float(box.conf[0]) * 100, 2)
            cls = int(box.cls[0])
            class_name = classNames[cls]

            # Filter out detections with confidence < 50%
            if confidence >= 50:
                # Extract bounding box coordinates
                x1, y1, x2, y2 = map(int, box.xyxy[0])

                # Draw bounding box
                cv2.rectangle(img, (x1, y1), (x2, y2), (255, 0, 255), 3)

                # Prepare label text (class name + confidence)
                label_text = f"{class_name}: {confidence}%"

                # Draw label on the image
                org = (x1, y1 - 10)  # Adjust position of label
                font = cv2.FONT_HERSHEY_SIMPLEX
                fontScale = 0.9
                color = (255, 0, 0)
                thickness = 2
                cv2.putText(img, label_text, org, font, fontScale, color, thickness)

    # Display the processed frame
    cv2.imshow('Webcam', img)

    # Check for 'q' key press to exit the loop
    if cv2.waitKey(1) == ord('q'):
        break

# Release resources
cap.release()
cv2.destroyAllWindows()


DEBUG:matplotlib:matplotlib data path: D:\Programs\anaconda3\lib\site-packages\matplotlib\mpl-data
DEBUG:matplotlib:CONFIGDIR=C:\Users\maeen\.matplotlib
DEBUG:matplotlib:interactive is False
DEBUG:matplotlib:platform is win32
DEBUG:matplotlib:CACHEDIR=C:\Users\maeen\.matplotlib
DEBUG:matplotlib.font_manager:Using fontManager instance from C:\Users\maeen\.matplotlib\fontlist-v330.json



0: 480x640 (no detections), 67.4ms
Speed: 2.9ms preprocess, 67.4ms inference, 16.1ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 8.0ms
Speed: 2.0ms preprocess, 8.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 8.0ms
Speed: 1.0ms preprocess, 8.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 8.0ms
Speed: 1.0ms preprocess, 8.0ms inference, 0.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 11.9ms
Speed: 2.0ms preprocess, 11.9ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 9.0ms
Speed: 1.0ms preprocess, 9.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 7.5ms
Speed: 1.0ms preprocess, 7.5ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 9.0ms
Speed: 2.0ms preprocess, 9.0ms inference, 1

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



0: 480x640 (no detections), 11.0ms
Speed: 3.0ms preprocess, 11.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 12.0ms
Speed: 2.0ms preprocess, 12.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 11.0ms
Speed: 2.0ms preprocess, 11.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 sunglasses, 11.0ms
Speed: 2.0ms preprocess, 11.0ms inference, 2.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 11.0ms
Speed: 2.0ms preprocess, 11.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 8.0ms
Speed: 2.0ms preprocess, 8.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 8.0ms
Speed: 1.0ms preprocess, 8.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 9.0ms
Speed: 1.0ms preprocess, 9.0ms inference, 

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



...

0: 480x640 (no detections), 7.9ms
Speed: 1.0ms preprocess, 7.9ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 8.0ms
Speed: 1.0ms preprocess, 8.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 headphone, 9.5ms
Speed: 1.0ms preprocess, 9.5ms inference, 2.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 13.0ms
Speed: 1.0ms preprocess, 13.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 8.7ms
Speed: 1.0ms preprocess, 8.7ms inference, 0.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 8.0ms
Speed: 1.0ms preprocess, 8.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 8.5ms
Speed: 1.0ms preprocess, 8.5ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 8.6ms
Speed: 1.0ms preprocess, 8.6ms inference, 0.0ms pos

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)




0: 480x640 (no detections), 9.0ms
Speed: 2.0ms preprocess, 9.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 11.9ms
Speed: 2.1ms preprocess, 11.9ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 9.0ms
Speed: 2.0ms preprocess, 9.0ms inference, 0.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 8.0ms
Speed: 2.6ms preprocess, 8.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 9.0ms
Speed: 2.0ms preprocess, 9.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 8.0ms
Speed: 2.0ms preprocess, 8.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 11.0ms
Speed: 2.0ms preprocess, 11.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 8.0ms
Speed: 2.0ms preprocess, 8.0ms inference, 1.

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)




0: 480x640 (no detections), 11.0ms
Speed: 2.0ms preprocess, 11.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 11.0ms
Speed: 2.0ms preprocess, 11.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 10.0ms
Speed: 1.0ms preprocess, 10.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 11.0ms
Speed: 2.0ms preprocess, 11.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 11.0ms
Speed: 1.0ms preprocess, 11.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 9.0ms
Speed: 1.0ms preprocess, 9.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 10.0ms
Speed: 1.0ms preprocess, 10.0ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 (no detections), 9.0ms
Speed: 1.0ms preprocess, 9.0ms infer

# Run First  IMPORTANT!

In [1]:
import os
os.environ["KMP_DUPLICATE_LIB_OK"]="TRUE"
# os.environ['CUDA_LAUNCH_BLOCKING'] = "1"
# os.environ["TORCH_USE_CUDA_DSA"] = "TRUE"
# import logging
# logging.basicConfig(level=logging.DEBUG) 

In [ ]:
jupyter-lab --NotebookApp.iopub_data_rate_limit=1.0e10

# Start training from a pretrained *.pt model

In [3]:
!yolo task=detect mode=train model="C:\Users\maeen\Object Detection\runs\detect\train43\weights\best.pt" data="C:\Users\maeen\Object Detection\datasets\Merged\data.yaml" epochs=250 imgsz=640 plots=True

New https://pypi.org/project/ultralytics/8.1.29 available ðŸ˜ƒ Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.1.27 ðŸš€ Python-3.10.9 torch-2.2.1+cu121 CUDA:0 (NVIDIA GeForce GTX 1080, 8192MiB)
engine\trainer: task=detect, mode=train, model=C:\Users\maeen\Object Detection\runs\detect\train43\weights\best.pt, data=C:\Users\maeen\Object Detection\datasets\Merged\data.yaml, epochs=250, time=None, patience=100, batch=16, imgsz=640, save=True, save_period=-1, cache=False, device=None, workers=8, project=None, name=train56, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visuali


train: Scanning C:\Users\maeen\Object Detection\datasets\Merged\train\labels\Male-Female...:   0%|          | 0/1055 [00:00<?, ?it/s]
train: Scanning C:\Users\maeen\Object Detection\datasets\Merged\train\labels\Male-Female... 214 images, 0 backgrounds, 0 corrupt:  20%|##        | 214/1055 [00:00<00:00, 2123.89it/s]
train: Scanning C:\Users\maeen\Object Detection\datasets\Merged\train\labels\Male-Female... 455 images, 0 backgrounds, 0 corrupt:  43%|####3     | 455/1055 [00:00<00:00, 2288.45it/s]
train: Scanning C:\Users\maeen\Object Detection\datasets\Merged\train\labels\Male-Female... 701 images, 0 backgrounds, 0 corrupt:  66%|######6   | 701/1055 [00:00<00:00, 2357.12it/s]
train: Scanning C:\Users\maeen\Object Detection\datasets\Merged\train\labels\Male-Female... 952 images, 0 backgrounds, 0 corrupt:  90%|######### | 952/1055 [00:00<00:00, 2410.32it/s]
train: Scanning C:\Users\maeen\Object Detection\datasets\Merged\train\labels\Male-Female... 1055 images, 3 backgrounds, 0 corrupt: 10

# Build a new model from YAML and start training from scratch

In [ ]:
!yolo task=detect mode=train data="C:\Users\maeen\Object Detection\datasets\SmartEye-Object-Detector\data.yaml" model="C:/Users/maeen/Object Detection/yolov8n.yaml" epochs=1 imgsz=640 plots=True

# Validate Model

In [ ]:
!yolo task=detect mode=val model="runs/detect/train36/weights/best.pt" data="C:/Users/maeen/Object Detection/datasets/data.yaml" conf=0.5

Ultralytics YOLOv8.1.27 ðŸš€ Python-3.10.9 torch-2.2.1+cu121 CUDA:0 (NVIDIA GeForce GTX 1080, 8192MiB)
YOLOv8 summary (fused): 168 layers, 3005843 parameters, 0 gradients, 8.1 GFLOPs



val: Scanning C:\Users\maeen\Object Detection\datasets\male\test\labels.cache... 7831 images, 291 backgrounds, 0 corrupt: 100%|##########| 7831/7831 [00:00<?, ?it/s]
val: Scanning C:\Users\maeen\Object Detection\datasets\male\test\labels.cache... 7831 images, 291 backgrounds, 0 corrupt: 100%|##########| 7831/7831 [00:00<?, ?it/s]

                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95):   0%|          | 0/490 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95):   0%|          | 1/490 [00:00<04:52,  1.67it/s]Exception in thread Thread-4 (plot_images):
Traceback (most recent call last):
  File "D:\Programs\anaconda3\lib\threading.py", line 1016, in _bootstrap_inner
    self.run()
  File "D:\Programs\anaconda3\lib\threading.py", line 953, in run
    self._target(*self._args, **self._kwargs)
  File "D:\Programs\anaconda3\lib\site-packages\ultralytics\utils\plotting.py", line 836, in plot_images
Exceptio

# Roboflow datasets

In [ ]:
!pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="0lzgQewgxsAh40uqRWs8")
project = rf.workspace("ai-project-hi3x8").project("test-rkuw2")
version = project.version(1)
dataset = version.download("yolov8")

In [ ]:
#-------------------------------------headphone----------------------------------
!pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="0lzgQewgxsAh40uqRWs8")
project = rf.workspace("yolov8workspace").project("headphones-detection-rx2oj")
version = project.version(1)
dataset = version.download("yolov8")
#--------------------------------------------------------------------------------

In [ ]:
#-------------------------------------Pen--------------------------------------
!pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="0lzgQewgxsAh40uqRWs8")
project = rf.workspace("yolov5-h3oo1").project("pen-zyj9j")
version = project.version(1)
dataset = version.download("yolov8")
#------------------------------------------------------------------------------- 

In [ ]:
#-------------------------------- Sun Glasses --------------------------------
!pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="0lzgQewgxsAh40uqRWs8")
project = rf.workspace("something-pggtn").project("e-ywa33")
version = project.version(1)
dataset = version.download("yolov8")
#------------------------------------------------------------------------------- 

In [ ]:
#--------------------------------- Breif Case ---------------------------------
!pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="0lzgQewgxsAh40uqRWs8")
project = rf.workspace("objek-dalam-5-ayunda").project("tas-model")
version = project.version(1)
dataset = version.download("yolov8")
#------------------------------------------------------------------------------- 

In [ ]:
#------------------------------------ Hats ------------------------------------
!pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="0lzgQewgxsAh40uqRWs8")
project = rf.workspace("objek-dalam-3-ayunda").project("topi-model")
version = project.version(1)
dataset = version.download("yolov8")
#-------------------------------------------------------------------------------

In [ ]:
#------------------------------------- Cups -------------------------------------
!pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="0lzgQewgxsAh40uqRWs8")
project = rf.workspace("kshitij-gera-b7cqa").project("vv-lk7zq")
version = project.version(2)
dataset = version.download("yolov8")
#-------------------------------------------------------------------------------

In [ ]:
#------------------------------------ Mouse ------------------------------------
!pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="0lzgQewgxsAh40uqRWs8")
project = rf.workspace("pnu-og7cn").project("mouse-vfvw6")
version = project.version(4)
dataset = version.download("yolov8")
#-------------------------------------------------------------------------------

In [ ]:
#------------------------------------ Shoes ------------------------------------
!pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="0lzgQewgxsAh40uqRWs8")
project = rf.workspace("amrlabs-n35ur").project("amr_shoes")
version = project.version(2)
dataset = version.download("yolov8")
#-------------------------------------------------------------------------------

In [ ]:
#-------------------------------- Mobile Phones --------------------------------
# !pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="0lzgQewgxsAh40uqRWs8")
project = rf.workspace("dhruv-kothiya-2khv5").project("screen-lzlq7")
version = project.version(1)
dataset = version.download("yolov8")
#-------------------------------------------------------------------------------

In [ ]:
#---------------------------------- Laptop ----------------------------------
!pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="0lzgQewgxsAh40uqRWs8")
project = rf.workspace("objek-dalam-ayunda").project("laptop-model-8h1yb")
version = project.version(1)
dataset = version.download("yolov8")
#-------------------------------------------------------------------------------

In [ ]:
#---------------------------------- Keyboard ----------------------------------
!pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="0lzgQewgxsAh40uqRWs8")
project = rf.workspace("fpt-university-1tkhk").project("kp-chych")
version = project.version(1)
dataset = version.download("yolov8")
#-------------------------------------------------------------------------------

In [ ]:
#------------------------------------ Bench ------------------------------------
!pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="0lzgQewgxsAh40uqRWs8")
project = rf.workspace("labaml").project("bench-detector")
version = project.version(1)
dataset = version.download("yolov8")
#-------------------------------------------------------------------------------

In [ ]:
#------------------------------------ Window ------------------------------------
!pip install roboflow

from roboflow import Roboflow
rf = Roboflow(api_key="0lzgQewgxsAh40uqRWs8")
project = rf.workspace("project-b3bvc").project("windows-detect")
version = project.version(3)
dataset = version.download("yolov8")
#-------------------------------------------------------------------------------

# Additional commands

In [ ]:
pip install --user --upgrade tensorflow numpy

In [ ]:
pip install tensorflow

In [ ]:
pip install -U ultralytics

In [ ]:
jupyter-lab --NotebookApp.iopub_data_rate_limit=1.0e10